In [ ]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/celeba-dataset/list_landmarks_align_celeba.csv
/kaggle/input/celeba-dataset/list_eval_partition.csv
/kaggle/input/celeba-dataset/list_attr_celeba.csv
/kaggle/input/celeba-dataset/list_bbox_celeba.csv
/kaggle/input/celeba-dataset/img_align_celeba/img_align_celeba/083648.jpg
/kaggle/input/celeba-dataset/img_align_celeba/img_align_celeba/168202.jpg
/kaggle/input/celeba-dataset/img_align_celeba/img_align_celeba/125778.jpg
/kaggle/input/celeba-dataset/img_align_celeba/img_align_celeba/059339.jpg
/kaggle/input/celeba-dataset/img_align_celeba/img_align_celeba/032501.jpg
/kaggle/input/celeba-dataset/img_align_celeba/img_align_celeba/160139.jpg
/kaggle/input/celeba-dataset/img_align_celeba/img_align_celeba/046754.jpg
/kaggle/input/celeba-dataset/img_align_celeba/img_align_celeba/178961.jpg
/kaggle/input/celeba-dataset/img_align_celeba/img_align_celeba/123482.jpg
/kaggle/input/celeba-dataset/img_align_celeba/img_align_celeba/039337.jpg
/kaggle/input/celeba-dataset/img_align_celeba/

In [5]:
!pip install tensorflow numpy pandas opencv-python matplotlib scikit-learn keras.utils keras keras.models

ERROR: Could not find a version that satisfies the requirement keras.utils (from versions: none)
ERROR: No matching distribution found for keras.utils


In [6]:
!pip install keras

In [9]:
model.save("nationality_age_model.h5")


In [4]:
import os
import pandas as pd
import numpy as np
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Conv2D, MaxPooling2D, Flatten, Dense, Dropout
from tensorflow.keras.preprocessing.image import load_img, img_to_array
from sklearn.model_selection import train_test_split

# Paths to data
celeba_dir = r"/kaggle/input/celeba-dataset/img_align_celeba/img_align_celeba"
attributes_file = r"/kaggle/input/celeba-dataset/list_attr_celeba.csv"

# Load attributes
attributes = pd.read_csv(attributes_file)

# Add synthetic age and nationality columns
np.random.seed(42)
attributes['age'] = np.random.randint(10, 61, size=len(attributes))
nationalities = ['Indian', 'United States', 'African', 'Other']
attributes['nationality'] = np.random.choice(nationalities, size=len(attributes))

# Create nationality mapping
nationality_mapping = {nat: i for i, nat in enumerate(nationalities)}
attributes['nationality'] = attributes['nationality'].map(nationality_mapping)

# Function to load and preprocess images
def load_and_preprocess_image(image_path):
    img = load_img(image_path, target_size=(128, 128))
    img_array = img_to_array(img) / 255.0
    return img_array

# Prepare data
num_samples = 10000  # Adjust this number based on your available memory
sample_df = attributes.sample(n=num_samples, random_state=42)

X = np.array([load_and_preprocess_image(os.path.join(celeba_dir, img_id)) for img_id in sample_df['image_id']])
y_nationality = np.array(sample_df['nationality'])
y_age = np.array(sample_df['age'])

# Split the data
X_train, X_test, y_nationality_train, y_nationality_test, y_age_train, y_age_test = train_test_split(
    X, y_nationality, y_age, test_size=0.2, random_state=42)

# Create the model using Functional API
inputs = Input(shape=(128, 128, 3))
x = Conv2D(32, (3, 3), activation='relu')(inputs)
x = MaxPooling2D((2, 2))(x)
x = Conv2D(64, (3, 3), activation='relu')(x)
x = MaxPooling2D((2, 2))(x)
x = Conv2D(64, (3, 3), activation='relu')(x)
x = Flatten()(x)
x = Dense(64, activation='relu')(x)
x = Dropout(0.5)(x)
nationality_output = Dense(len(nationalities), activation='softmax', name='nationality_output')(x)
age_output = Dense(1, activation='linear', name='age_output')(x)

model = Model(inputs=inputs, outputs=[nationality_output, age_output])

# Compile the model
model.compile(optimizer='adam',
              loss={'nationality_output': 'sparse_categorical_crossentropy', 'age_output': 'mse'},
              loss_weights={'nationality_output': 1.0, 'age_output': 0.5},
              metrics={'nationality_output': 'accuracy', 'age_output': 'mae'})

# Train the model
history = model.fit(
    X_train,
    {'nationality_output': y_nationality_train, 'age_output': y_age_train},
    validation_data=(X_test, {'nationality_output': y_nationality_test, 'age_output': y_age_test}),
    epochs=10,
    batch_size=32
)

# Save the model
model.save("nationality_age_model.h5")

print("Model training completed and saved as 'nationality_age_model.h5'")


Epoch 1/10
250/250 ━━━━━━━━━━━━━━━━━━━━ 131s 513ms/step - age_output_mae: 15.5357 - loss: 193.2146 - nationality_output_accuracy: 0.2650 - val_age_output_mae: 12.6740 - val_loss: 109.5630 - val_nationality_output_accuracy: 0.2395
Epoch 2/10
250/250 ━━━━━━━━━━━━━━━━━━━━ 109s 437ms/step - age_output_mae: 13.6909 - loss: 138.8595 - nationality_output_accuracy: 0.2462 - val_age_output_mae: 12.6540 - val_loss: 109.1207 - val_nationality_output_accuracy: 0.2620
Epoch 3/10
250/250 ━━━━━━━━━━━━━━━━━━━━ 142s 437ms/step - age_output_mae: 13.4605 - loss: 129.9797 - nationality_output_accuracy: 0.2421 - val_age_output_mae: 12.7215 - val_loss: 111.4561 - val_nationality_output_accuracy: 0.2620
Epoch 4/10
250/250 ━━━━━━━━━━━━━━━━━━━━ 109s 434ms/step - age_output_mae: 13.6990 - loss: 132.3722 - nationality_output_accuracy: 0.2398 - val_age_output_mae: 12.7359 - val_loss: 111.8370 - val_nationality_output_accuracy: 0.2310
Epoch 5/10
250/250 ━━━━━━━━━━━━━━━━━━━━ 141s 430ms/step - age_output_mae: 13.572

In [6]:
model.save("nationality_age_model.h5")


In [3]:
model.summary()


Model: "functional_1"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer         │ (None, 200, 200,  │          0 │ -                 │
│ (InputLayer)        │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d (Conv2D)     │ (None, 200, 200,  │        896 │ input_layer[0][0] │
│                     │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ max_pooling2d       │ (None, 100, 100,  │          0 │ conv2d[0][0]      │
│ (MaxPooling2D)      │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_1 (Conv2D)   │ (None, 100, 100,  │     18,496 │ max_pooling2d[0]… │
│                     │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ max_pooling2d_1     │ (None, 50, 50,    │          0 │ conv2d_1[0][0]    │
│ (MaxPooling2D)      │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_2 (Conv2D)   │ (None, 50, 50,    │     73,856 │ max_pooling2d_1[… │
│                     │ 128)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ max_pooling2d_2     │ (None, 25, 25,    │          0 │ conv2d_2[0][0]    │
│ (MaxPooling2D)      │ 128)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ flatten (Flatten)   │ (None, 80000)     │          0 │ max_pooling2d_2[… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense (Dense)       │ (None, 128)       │ 10,240,128 │ flatten[0][0]     │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ emotion (Dense)     │ (None, 7)         │        903 │ dense[0][0]       │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ age (Dense)         │ (None, 1)         │        129 │ dense[0][0]       │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ nationality (Dense) │ (None, 4)         │        516 │ dense[0][0]       │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dress_color (Dense) │ (None, 5)         │        645 │ dense[0][0]       │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 10,335,569 (39.43 MB)

 Trainable params: 10,335,569 (39.43 MB)

 Non-trainable params: 0 (0.00 B)

In [9]:
import os
import pandas as pd
import numpy as np
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Conv2D, MaxPooling2D, Flatten, Dense, Dropout, BatchNormalization
from tensorflow.keras.preprocessing.image import load_img, img_to_array, ImageDataGenerator
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, mean_absolute_error

# Paths to data
celeba_dir = "/kaggle/input/celeba-dataset/img_align_celeba/img_align_celeba"
attributes_file = "/kaggle/input/celeba-dataset/list_attr_celeba.csv"

# Load attributes
attributes = pd.read_csv(attributes_file)

# Add synthetic age and nationality columns
np.random.seed(42)
attributes['age'] = np.random.randint(10, 61, size=len(attributes))
nationalities = ['Indian', 'United States', 'African', 'Other']
attributes['nationality'] = np.random.choice(nationalities, size=len(attributes))

# Create nationality mapping
nationality_mapping = {nat: i for i, nat in enumerate(nationalities)}
attributes['nationality'] = attributes['nationality'].map(nationality_mapping)

# Function to load and preprocess images
def load_and_preprocess_image(image_path):
    img = load_img(image_path, target_size=(128, 128))
    img_array = img_to_array(img) / 255.0
    return img_array

# Prepare data
num_samples = 10000  # Adjust this number based on your available memory
sample_df = attributes.sample(n=num_samples, random_state=42)

X = np.array([load_and_preprocess_image(os.path.join(celeba_dir, img_id)) for img_id in sample_df['image_id'].values])
y_nationality = np.array(sample_df['nationality'])
y_age = np.array(sample_df['age'])

# Split the data
X_train, X_test, y_nationality_train, y_nationality_test, y_age_train, y_age_test = train_test_split(
    X, y_nationality, y_age, test_size=0.2, random_state=42)

# Data Augmentation
datagen = ImageDataGenerator(
    rotation_range=20,
    width_shift_range=0.2,
    height_shift_range=0.2,
    horizontal_flip=True
)
datagen.fit(X_train)

# Create the model using Functional API
inputs = Input(shape=(128, 128, 3))
x = Conv2D(32, (3, 3), activation='relu')(inputs)
x = BatchNormalization()(x)
x = MaxPooling2D((2, 2))(x)
x = Conv2D(64, (3, 3), activation='relu')(x)
x = BatchNormalization()(x)
x = MaxPooling2D((2, 2))(x)
x = Conv2D(128, (3, 3), activation='relu')(x)
x = BatchNormalization()(x)
x = MaxPooling2D((2, 2))(x)
x = Flatten()(x)
x = Dense(128, activation='relu')(x)
x = Dropout(0.5)(x)
nationality_output = Dense(len(nationalities), activation='softmax', name='nationality_output')(x)
age_output = Dense(1, activation='linear', name='age_output')(x)

model = Model(inputs=inputs, outputs=[nationality_output, age_output])

# Compile the model
model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate=0.001),
              loss={'nationality_output': 'sparse_categorical_crossentropy', 'age_output': 'mse'},
              loss_weights={'nationality_output': 1.0, 'age_output': 0.5},
              metrics={'nationality_output': 'accuracy', 'age_output': 'mae'})

# Train the model
history = model.fit(
    X_train,
    {'nationality_output': y_nationality_train, 'age_output': y_age_train},
    validation_data=(X_test, {'nationality_output': y_nationality_test, 'age_output': y_age_test}),
    epochs=50,
    batch_size=32,
    callbacks=[
        tf.keras.callbacks.EarlyStopping(patience=5, restore_best_weights=True),
        tf.keras.callbacks.ReduceLROnPlateau(factor=0.2, patience=3)
    ]
)

# Save the model
model.save("optimized_nationality_age_model.h5")

print("Model training completed and saved as 'optimized_nationality_age_model.h5'")

# Evaluate the model
predictions = model.predict(X_test)
nationality_predictions = np.argmax(predictions[0], axis=1)
age_predictions = predictions[1].flatten()

nationality_accuracy = accuracy_score(y_nationality_test, nationality_predictions)
print(f'Nationality Prediction Accuracy: {nationality_accuracy * 100:.2f}%')

age_mae = mean_absolute_error(y_age_test, age_predictions)
print(f'Age Prediction Mean Absolute Error: {age_mae:.2f}')

accuracy_within_5_years = np.mean(np.abs(age_predictions - y_age_test) <= 5) * 100
print(f'Accuracy within 5 years for Age Prediction: {accuracy_within_5_years:.2f}%')

Epoch 1/50
250/250 ━━━━━━━━━━━━━━━━━━━━ 266s 1s/step - age_output_mae: 15.9163 - loss: 201.4281 - nationality_output_accuracy: 0.2563 - val_age_output_mae: 14.7113 - val_loss: 166.1619 - val_nationality_output_accuracy: 0.2455 - learning_rate: 0.0010
Epoch 2/50
250/250 ━━━━━━━━━━━━━━━━━━━━ 328s 1s/step - age_output_mae: 14.4038 - loss: 157.0728 - nationality_output_accuracy: 0.2516 - val_age_output_mae: 13.4865 - val_loss: 126.6993 - val_nationality_output_accuracy: 0.2455 - learning_rate: 0.0010
Epoch 3/50
250/250 ━━━━━━━━━━━━━━━━━━━━ 322s 1s/step - age_output_mae: 13.7900 - loss: 142.1512 - nationality_output_accuracy: 0.2585 - val_age_output_mae: 13.4321 - val_loss: 131.1644 - val_nationality_output_accuracy: 0.2500 - learning_rate: 0.0010
Epoch 4/50
250/250 ━━━━━━━━━━━━━━━━━━━━ 264s 1s/step - age_output_mae: 13.5384 - loss: 135.3623 - nationality_output_accuracy: 0.2645 - val_age_output_mae: 13.5670 - val_loss: 135.6024 - val_nationality_output_accuracy: 0.2390 - learning_rate: 0.0